In [1]:
import geopandas as gpd
import rasterio
from rasterio.features import geometry_mask
from rasterio.transform import from_origin
import numpy as np

merged = gpd.read_file('cmdx_mza_reproyectado_censo.shp')


In [2]:
import geopandas as gpd
from rasterio.plot import show
import rasterio
from rasterio.features import geometry_mask
from rasterio.transform import from_origin
import numpy as np

# Cargamos el GeoDataFrame
gdf = merged

# Definimos la resolución y las dimensiones del raster
res = 30 # Resolución en metros
bounds = gdf.total_bounds
width = int((bounds[2] - bounds[0]) / res)
height = int((bounds[3] - bounds[1]) / res)

# Creamos un raster vacío
out_arr = np.zeros((height, width), dtype=np.float32)

# Creamos la transformación
transform = from_origin(bounds[0], bounds[3], res, res)

# Iteramos sobre las filas del GeoDataFrame
for index, row in gdf.iterrows():
    # Creamos una máscara para las celdas del raster que caen dentro del polígono
    mask = geometry_mask([row.geometry], transform=transform, out_shape=(height, width), invert=True)
    
    # Calculamos el área de cada celda de raster que cae dentro del polígono
    cell_area = mask.sum() * res * res
    
    # Dividimos la población del polígono de manera proporcional al área de cada celda de raster
    out_arr[mask] = row['POBTOT'] / cell_area

# Guardamos el resultado en un nuevo archivo raster
with rasterio.open('poblacion.tif', 'w', driver='GTiff', height=height, width=width, count=1, dtype=str(out_arr.dtype), crs=gdf.crs, transform=transform) as dst:
    dst.write(out_arr, 1)

C:\Users\MI18877\AppData\Local\Temp\1\ipykernel_43688\361571943.py:32: RuntimeWarning: divide by zero encountered in long_scalars
  out_arr[mask] = row['POBTOT'] / cell_area
C:\Users\MI18877\AppData\Local\Temp\1\ipykernel_43688\361571943.py:32: RuntimeWarning: divide by zero encountered in long_scalars
  out_arr[mask] = row['POBTOT'] / cell_area
C:\Users\MI18877\AppData\Local\Temp\1\ipykernel_43688\361571943.py:32: RuntimeWarning: divide by zero encountered in long_scalars
  out_arr[mask] = row['POBTOT'] / cell_area
C:\Users\MI18877\AppData\Local\Temp\1\ipykernel_43688\361571943.py:32: RuntimeWarning: divide by zero encountered in long_scalars
  out_arr[mask] = row['POBTOT'] / cell_area
C:\Users\MI18877\AppData\Local\Temp\1\ipykernel_43688\361571943.py:32: RuntimeWarning: divide by zero encountered in long_scalars
  out_arr[mask] = row['POBTOT'] / cell_area
C:\Users\MI18877\AppData\Local\Temp\1\ipykernel_43688\361571943.py:32: RuntimeWarning: divide by zero encountered in long_scalars


In [3]:
import numpy as np
from rasterio import Affine

# Leer el archivo raster creado previamente
output_raster_path = 'poblacion.tif'
normalized_raster_path = 'poblacion_normalizada.tif'

with rasterio.open(output_raster_path) as src:
    saved_raster_data = src.read(1)
    saved_raster_data_normalized = (saved_raster_data - np.min(saved_raster_data)) / (np.max(saved_raster_data) - np.min(saved_raster_data))  # Normalizar los datos
    raster_transform = src.transform
    profile = src.profile

# Guardar el raster normalizado
with rasterio.open(normalized_raster_path, 'w', **profile) as dst:
    dst.write(saved_raster_data_normalized, 1)

# Imprimir los valores únicos del raster original y del raster normalizado
unique_values_original = np.unique(saved_raster_data)
unique_values_normalized = np.unique(saved_raster_data_normalized)

print("Valores únicos en el raster original: ", unique_values_original)
print("Valores únicos en el raster normalizado: ", unique_values_normalized)


Valores únicos en el raster original:  [0.0000000e+00 3.1167212e-06 5.4600055e-06 ... 1.5177778e+00 1.6733333e+00
 4.3000002e+00]
Valores únicos en el raster normalizado:  [0.0000000e+00 7.2481885e-07 1.2697686e-06 ... 3.5297155e-01 3.8914725e-01
 1.0000000e+00]


In [4]:
import numpy as np
import matplotlib.colors as colors
from rasterio.plot import show
import matplotlib.pyplot as plt

# Leer el archivo raster creado previamente
output_raster_path = 'poblacion_normalizada.tif'
with rasterio.open(output_raster_path) as src:
    saved_raster_data = src.read(1)
   # saved_raster_data = np.log(saved_raster_data + 1)  # Aplicar transformación logarítmica
    raster_transform = src.transform

# Visualizar el archivo rasterizado
fig, ax = plt.subplots(figsize=(120, 120))

# Definir una normalización logarítmica para los colores
color_norm = colors.LogNorm(vmin=saved_raster_data.min(), vmax=saved_raster_data.max())

show(saved_raster_data, transform=raster_transform, ax=ax, cmap=plt.cm.inferno, norm=color_norm)

ax.set_title("Peso de uso de suelo en relación con la distribución de la población en la Ciudad de México (rasterizado)")
ax.set_xlabel("Longitud")
ax.set_ylabel("Latitud")

plt.show()


In [5]:
# Cargamos el archivo shapefile
cdmx = gpd.read_file('C:/Users/MI18877/Auto-GPT/auto_gpt_workspace/Tesis/inegi/mgccpv/09_ciudaddemexico/conjunto_de_datos/09ent.shp')